In [1]:
# Imports
import os

import numpy as np

import rclpy
from rclpy.node import Node

import rosbag2_py
from rclpy.serialization import deserialize_message
from rosidl_runtime_py.utilities import get_message
# from rclpy.wait_for_message import wait_for_message

# from sensor_msgs.msg import Image
# from audio_common_msgs.msg import AudioDataStamped
# from vision_msgs.msg import Detection3DArray
# from tracking_msgs.msg import Detections3D
# from situated_hri_interfaces.srv import SceneVisRec, SceneAudioRec, RecordEpoch
# from tf2_msgs.msg import TFMessage

# from std_srvs.srv import Empty

from PIL import Image as PILImage
import cv2
import cv_bridge

In [10]:
### from the top, just read the bag and do the recognition here

# Parameters
filepath = '../../bags/e1_est_tuning'

# Other member variables
actual_scene_labels = ['campus','courtyard','lab','lobby']
bridge = cv_bridge.CvBridge()

# Helper functions
def typename(topic_name):
    for topic_type in topic_types:
        if topic_type.name == topic_name:
            return topic_type.type
    raise ValueError(f"topic {topic_name} not in bag")

# Traverse filepath
for root, _, files in os.walk(filepath):

    # Examine each file
    for file in files:
        
        # If it is an mcap, examine
        if os.path.splitext(file)[-1] == '.mcap':

            # Get labels based on filepath
            labels = os.path.normpath(root).split(os.sep)
            command_actual = labels[-1]
            cmd_mode_actual = labels[-2]
            role_actual = labels[-3]
            scene_actual = labels[-4]
            iteration = os.path.splitext(file)[-2].split('_')[-1]

            scene_actual_idx = actual_scene_labels.index(scene_actual)
            
            print('Command: %s\nModality: %s\nRole: %s\nScene: %s (%s)\n\n' % (command_actual, cmd_mode_actual, role_actual, scene_actual, scene_actual_idx))

            # Create reader object           
            reader = rosbag2_py.SequentialReader()            
            reader.open(
                rosbag2_py.StorageOptions(uri=os.path.join(root,file), storage_id="mcap"),
                rosbag2_py.ConverterOptions(
                    input_serialization_format="cdr", output_serialization_format="cdr"
                ),
            )
            topic_types = reader.get_all_topics_and_types()

            # Iterate through messages
            img_received = False
            while reader.has_next():
                topic, data, timestamp = reader.read_next()
                msg_type = get_message(typename(topic))

                if topic=='/oak/rgb/image_raw':
                    latest_img_msg = deserialize_message(data,msg_type)
                    img_received = True

                if topic=='/oak/nn/spatial_detections':
                    if img_received:

                        latest_det_msg = deserialize_message(data,msg_type)
                        for det in latest_det_msg.detections:

                            # look for human detected ~3m in front of camera
                            dist_to_3m_in_front = np.linalg.norm([det.results[0].pose.pose.position.x,det.results[0].pose.pose.position.y, det.results[0].pose.pose.position.z - 3.])
                            
                            if (dist_to_3m_in_front < 0.5 and det.results[0].hypothesis.class_id=='0'):
                                
                                cv_image = bridge.imgmsg_to_cv2(latest_img_msg, desired_encoding='rgb8')

                                bbox_center_x = det.bbox.center.position.x
                                bbox_center_y = det.bbox.center.position.y
                                bbox_size_x = det.bbox.size.x
                                bbox_size_y = det.bbox.size.y

                        
                        # // Generate mask, mask cv_in and publish
                        # // Compute mask pixel locations
                        # float scale = (float)std::min(cv_in_->image.rows, cv_in_->image.cols)/(float)nn_img_size;
                        # int x_off = (cv_in_->image.cols - std::min(cv_in_->image.rows, cv_in_->image.cols))/2;
                        # int y_off = (cv_in_->image.rows - std::min(cv_in_->image.rows, cv_in_->image.cols))/2;
        
                        # int xmin = x_off + std::max(0, (int)(scale*(it->bbox.center.position.x - (it->bbox.size.x)/2)));
                        # int ymin = y_off + std::max(0, (int)(scale*(it->bbox.center.position.y - (it->bbox.size.y)/2)));
                        # int xmax = x_off + std::min(std::min(cv_in_->image.rows, cv_in_->image.cols), (int)(scale*(it->bbox.center.position.x + (it->bbox.size.x)/2)));
                        # int ymax = y_off + std::min(std::min(cv_in_->image.rows, cv_in_->image.cols), (int)(scale*(it->bbox.center.position.y + (it->bbox.size.y)/2)));
        
                        # cv::Mat cv_out_mat = cv_in_->image(cv::Range(ymin, ymax),cv::Range(xmin, xmax));
        
                        # cv_out_.header = cv_in_->header;
                        # cv_out_.encoding = cv_in_->encoding;
                        # cv_out_.image = cv_out_mat;
        
                        # img_out_ = cv_out_.toImageMsg();
                
            del reader



Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-forward
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-forward
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-forward
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-forward
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: move-forward
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: follow-me
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: follow-me
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Command: follow-me
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Comman

KeyboardInterrupt: 

In [11]:
cv_mat = cv2.Mat(cv_image)
cv_mat.shape

(720, 1280, 3)

In [12]:
nn_img_size = 416

rows = cv_mat.shape[0]
cols = cv_mat.shape[1]

scale = np.min([rows,cols])/nn_img_size
x_off = int((cols - np.min([rows,cols]))/2)
y_off = int((rows - np.min([rows,cols]))/2)
print(x_off)
print(y_off)


x_min = x_off + np.max([0, int(scale*(bbox_center_x - bbox_size_x/2))])
y_min = y_off + np.max([0, int(scale*(bbox_center_y - bbox_size_y/2))])
x_max = x_off + np.min([np.min([rows, cols]), int(scale*(bbox_center_x + bbox_size_x/2))])
y_max = y_off + np.min([np.min([rows, cols]), int(scale*(bbox_center_y + bbox_size_y/2))])

print("x: %s, %s" % (x_min, x_max))
print("y: %s, %s" % (y_min, y_max))

280
0
x: 534, 731
y: 96, 720


In [13]:

print(cv_image.shape)



pil_img = PILImage.fromarray(cv_image[y_min:y_max,x_min:x_max,:])

(720, 1280, 3)


In [14]:
pil_img.show()

/snap/core20/current/lib/x86_64-linux-gnu/libstdc++.so.6: version `GLIBCXX_3.4.29' not found (required by /lib/x86_64-linux-gnu/libproxy.so.1)
Failed to load module: /home/jd/snap/code/common/.cache/gio-modules/libgiolibproxy.so
Gtk-Message: 11:17:53.833: Failed to load module "canberra-gtk-module"
Gtk-Message: 11:17:53.834: Failed to load module "canberra-gtk-module"


In [2]:
# Parameters
filepath = '../../bags/e1_est_tuning'

In [3]:
# Member variables
rclpy.init()
node = Node('analysis_script_node')

# Set parameters


# Create custom Quality of Service profile to avoid errors with tf_static playback
tf_static_qos = rclpy.qos.QoSProfile(history = rclpy.qos.HistoryPolicy.KEEP_LAST, 
                                     depth = 10,
                                     reliability = rclpy.qos.ReliabilityPolicy.RELIABLE,
                                     durability = rclpy.qos.DurabilityPolicy.TRANSIENT_LOCAL)

# Publishers
img_data_pub = node.create_publisher(Image, 'oak/rgb/image_raw',10)
oakd_det_pub = node.create_publisher(Detection3DArray, 'oak/nn/spatial_detections',10)
tf_pub = node.create_publisher(TFMessage, 'tf',10)
tf_static_pub = node.create_publisher(TFMessage, 'tf_static', tf_static_qos)

# Other member variables
actual_scene_labels = ['campus','courtyard','lab','lobby']
static_tf_sent = False
tf_sent = False

# Helper functions
def typename(topic_name):
    for topic_type in topic_types:
        if topic_type.name == topic_name:
            return topic_type.type
    raise ValueError(f"topic {topic_name} not in bag")

In [9]:
rclpy.shutdown()

In [ ]:
# Traverse filepath
for root, dirs, files in os.walk(filepath):

    # Examine each file
    for file in files:
        
        # If it is an mcap, examine
        if os.path.splitext(file)[-1] == '.mcap':

            # Get labels based on filepath
            labels = os.path.normpath(root).split(os.sep)
            command_actual = labels[-1]
            cmd_mode_actual = labels[-2]
            role_actual = labels[-3]
            scene_actual = labels[-4]
            iteration = os.path.splitext(file)[-2].split('_')[-1]

            scene_actual_idx = actual_scene_labels.index(scene_actual)
            
            print('Command: %s\nModality: %s\nRole: %s\nScene: %s (%s)\n\n' % (command_actual, cmd_mode_actual, role_actual, scene_actual, scene_actual_idx))

            # Start recording results for this epoch
            record_epoch_req = RecordEpoch.Request()
            record_epoch_req.scene = scene_actual
            record_epoch_req.role = role_actual
            record_epoch_req.cmd_mode = cmd_mode_actual
            record_epoch_req.cmd = command_actual
            record_epoch_req.iteration = int(iteration)
            
            reader = rosbag2_py.SequentialReader()            
            reader.open(
                rosbag2_py.StorageOptions(uri=os.path.join(root,file), storage_id="mcap"),
                rosbag2_py.ConverterOptions(
                    input_serialization_format="cdr", output_serialization_format="cdr"
                ),
            )
            topic_types = reader.get_all_topics_and_types()

            # Iterate through messages
            while reader.has_next():
                topic, data, timestamp = reader.read_next()
                msg_type = get_message(typename(topic))

                if topic=='/oak/rgb/image_raw':
                    img_data_pub.publish(deserialize_message(data,msg_type))

                if topic=='/oak/nn/spatial_detections':
                    if static_tf_sent:
                        print('Sending spatial dets message')
                        oakd_det_pub.publish(deserialize_message(data,msg_type))
                        print('Sent spatial dets message')

                        # Wait for messages
                        ret, converted_det_msg = wait_for_message(Detections3D, node, 'converted_img_detections', time_to_wait=1)
    
                        # Ensure you get a response!
                        while ret is False:
                            print('No response received')
                            oakd_det_pub.publish(deserialize_message(data,msg_type))
                            print('Sent spatial dets message')
                            ret, converted_det_msg = wait_for_message(Detections3D, node, 'converted_img_detections', time_to_wait=1)

                        
                        print('Processing converted dets')
                        print(converted_det_msg)
                        for det in converted_det_msg.detections:
                            print('got a det!')
                        
                        # TODO CHECK IF IT IS HUMAN AND SEND IT
                
                        # TODO - send to clip and wait for response
                
                    # TODO - log it/update model
                
                if topic=='/tf':
                    tf_pub.publish(deserialize_message(data,msg_type))
                    tf_sent = True
                    
                if topic=='/tf_static':
                    tf_static_pub.publish(deserialize_message(data,msg_type))
                    static_tf_sent = True
                
            del reader


# Cleanup
stop_tracker_recording_future = stop_tracker_recording_client.call_async(Empty.Request())
rclpy.spin_until_future_complete(node, stop_tracker_recording_future)

rclpy.shutdown()

Command: move-in-reverse
Modality: gest_verb
Role: supervisor
Scene: lab (2)


Sending spatial dets message
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received
Sent spatial dets message
No response received

In [ ]:
# For file in filepath, get scene, role, modality, and command

# Reset estimator nodes

# LAST - Load new parameters

# Play bag file

# Record scene responses - audio, visual, fused

# Record command responses - ARtag, speech, gesture, fused

In [5]:
rclpy.wait_for_message

TypeError: wait_for_message() missing 3 required positional arguments: 'msg_type', 'node', and 'topic'